# Assignment 3

Import libraries and define common helper functions

In [70]:
import os
import sys
import gzip
import json
from pathlib import Path
import csv

import pandas as pd
import s3fs
import pyarrow as pa
from pyarrow.json import read_json
import pyarrow.parquet as pq
import fastavro
import pygeohash
import snappy
import jsonschema
from jsonschema.exceptions import ValidationError


endpoint_url='https://storage.budsc.midwest-datascience.com'

current_dir = Path(os.getcwd()).absolute()
schema_dir = current_dir.joinpath('schemas')
results_dir = current_dir.joinpath('results')
results_dir.mkdir(parents=True, exist_ok=True)


def read_jsonl_data():
    s3 = s3fs.S3FileSystem(
        anon=True,
        client_kwargs={
            'endpoint_url': endpoint_url
        }
    )
    src_data_path = 'data/processed/openflights/routes.jsonl.gz'
    with s3.open(src_data_path, 'rb') as f_gz:
        with gzip.open(f_gz, 'rb') as f:
            records = [json.loads(line) for line in f.readlines()]
        

    return records

Load the records from https://storage.budsc.midwest-datascience.com/data/processed/openflights/routes.jsonl.gz 

In [71]:
records = read_jsonl_data()

In [3]:
len(records)

67663

## 3.1

### 3.1.a JSON Schema

In [3]:
def validate_jsonl_data(records):
    schema_path = schema_dir.joinpath('routes-schema.json')
    with open(schema_path) as f:
        schema = json.load(f)
#         print(schema)
    validation_csv_path = results_dir.joinpath('validation-results.csv')    
    with open(validation_csv_path, 'w', newline='') as f:    
        writer = csv.writer(f)
        for i, record in enumerate(records):
            try:
                ## TODO: Validate record 
#                 print(i)#,'\n', record,'\n')
                jsonschema.validate(record, schema)
#                 pass
            except ValidationError as e:
                ## Print message if invalid record
#                 print(e)
#                 print(f"Error: {e.message}; failed validating {e.validator} in schema {e.schema_path}")
                f.write(f"Error: {e.message}; failed validating {e.validator} in schema {e.schema_path}\r\n")
#                 writer.writerows(f"Error: {e.message}; failed validating {e.validator} in schema {e.schema_path}")
#                 return e
                print(e)
#                 print("message", e.message) # the issue 'None is not a type of object'
#                 print("context", e.context)
#                 print("cause", e.cause) # the value causing the issue
#                 print("instance", e.instance) # the value causing the issue
#                 print("json_path", e.json_path)
#                 print("path", e.path) # tells which section of json has the issue 'src_airport'
#                 print("schema", e.schema)
#                 print("schema_path", e.schema_path) # which section with more info 'properties', 'src_airport', 'type'
#                 print("validator", e.validator) # type
#                 print("validator_value", e.validator_value) # object
#                 print("relative_path", e.relative_path) # 'src_airport'
#                 print("absolute_path", e.absolute_path) # 'src_airport'
#                 print("parent", e.parent) # None (if NA)
#                 print("Error in record",i,":\n", e)
#                 pass
            

validate_jsonl_data(records)

### 3.1.b Avro

In [72]:
schema_path = schema_dir.joinpath('routes.avsc')
print(schema_path)
data_path = results_dir.joinpath('routes.avro')
print(data_path)

/home/jovyan/dsc650/dsc650/assignments/assignment03/schemas/routes.avsc
/home/jovyan/dsc650/dsc650/assignments/assignment03/results/routes.avro


In [23]:
# with open(schema_path) as f:
#     schema = json.load(f)
# # schema

In [ ]:
# records = [json.loads(line) for line in f.readlines()]

In [74]:
# data_path = results_dir.joinpath('routes.avro')

# from fastavro import reader
# with open(data_path, 'rb') as fo:
#     avro_reader = reader(fo)
#     for record in avro_reader:
#         print(record)

{'airline': {'airline_id': 410, 'name': 'Aerocondor', 'alias': 'ANA All Nippon Airways', 'iata': '2B', 'icao': 'ARD', 'callsign': 'AEROCONDOR', 'country': 'Portugal', 'active': True}, 'src_airport': {'airport_id': 2965, 'name': 'Sochi International Airport', 'city': 'Sochi', 'iata': 'AER', 'icao': 'URSS', 'latitude': 43.449902, 'longitude': 39.9566, 'timezone': 3.0, 'dst': 'N', 'tz_id': 'Europe/Moscow', 'type': 'airport', 'source': 'OurAirports'}, 'dst_airport': {'airport_id': 2990, 'name': 'Kazan International Airport', 'city': 'Kazan', 'iata': 'KZN', 'icao': 'UWKD', 'latitude': 55.606201171875, 'longitude': 49.278701782227, 'timezone': 3.0, 'dst': 'N', 'tz_id': 'Europe/Moscow', 'type': 'airport', 'source': 'OurAirports'}, 'codeshare': False, 'stops': 0, 'equipment': ['CR2']}
{'airline': {'airline_id': 410, 'name': 'Aerocondor', 'alias': 'ANA All Nippon Airways', 'iata': '2B', 'icao': 'ARD', 'callsign': 'AEROCONDOR', 'country': 'Portugal', 'active': True}, 'src_airport': {'airport_id'

{'airline': {'airline_id': 2548, 'name': 'Germanwings', 'alias': 'FlyAsianXpress', 'iata': '4U', 'icao': 'GWI', 'callsign': 'GERMAN WINGS', 'country': 'Germany', 'active': True}, 'src_airport': {'airport_id': 344, 'name': 'Cologne Bonn Airport', 'city': 'Cologne', 'iata': 'CGN', 'icao': 'EDDK', 'latitude': 50.865898132299996, 'longitude': 7.1427397728, 'timezone': 1.0, 'dst': 'E', 'tz_id': 'Europe/Berlin', 'type': 'airport', 'source': 'OurAirports'}, 'dst_airport': {'airport_id': 342, 'name': 'Hamburg Airport', 'city': 'Hamburg', 'iata': 'HAM', 'icao': 'EDDH', 'latitude': 53.630401611328004, 'longitude': 9.988229751586902, 'timezone': 1.0, 'dst': 'E', 'tz_id': 'Europe/Berlin', 'type': 'airport', 'source': 'OurAirports'}, 'codeshare': False, 'stops': 0, 'equipment': ['319', 'CRJ']}
{'airline': {'airline_id': 2548, 'name': 'Germanwings', 'alias': 'FlyAsianXpress', 'iata': '4U', 'icao': 'GWI', 'callsign': 'GERMAN WINGS', 'country': 'Germany', 'active': True}, 'src_airport': {'airport_id':

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



{'airline': {'airline_id': 4296, 'name': 'Ryanair', 'alias': 'Qantas Airways', 'iata': 'FR', 'icao': 'RYR', 'callsign': 'RYANAIR', 'country': 'Ireland', 'active': True}, 'src_airport': {'airport_id': 691, 'name': 'Gothenburg City Airport', 'city': 'Gothenborg', 'iata': 'GSE', 'icao': 'ESGP', 'latitude': 57.7747, 'longitude': 11.8704, 'timezone': 1.0, 'dst': 'E', 'tz_id': 'Europe/Stockholm', 'type': 'airport', 'source': 'OurAirports'}, 'dst_airport': {'airport_id': 535, 'name': 'Edinburgh Airport', 'city': 'Edinburgh', 'iata': 'EDI', 'icao': 'EGPH', 'latitude': 55.95000076293945, 'longitude': -3.372499942779541, 'timezone': 0.0, 'dst': 'E', 'tz_id': 'Europe/London', 'type': 'airport', 'source': 'OurAirports'}, 'codeshare': False, 'stops': 0, 'equipment': ['738']}
{'airline': {'airline_id': 4296, 'name': 'Ryanair', 'alias': 'Qantas Airways', 'iata': 'FR', 'icao': 'RYR', 'callsign': 'RYANAIR', 'country': 'Ireland', 'active': True}, 'src_airport': {'airport_id': 691, 'name': 'Gothenburg Ci

{'airline': {'airline_id': 35, 'name': 'Allegiant Air', 'alias': '\\N', 'iata': 'G4', 'icao': 'AAY', 'callsign': 'ALLEGIANT', 'country': 'United States', 'active': True}, 'src_airport': {'airport_id': 4046, 'name': 'General Wayne A. Downing Peoria International Airport', 'city': 'Peoria', 'iata': 'PIA', 'icao': 'KPIA', 'latitude': 40.664199829100006, 'longitude': -89.6932983398, 'timezone': -6.0, 'dst': 'A', 'tz_id': 'America/Chicago', 'type': 'airport', 'source': 'OurAirports'}, 'dst_airport': {'airport_id': 3617, 'name': 'St Petersburg Clearwater International Airport', 'city': 'St. Petersburg', 'iata': 'PIE', 'icao': 'KPIE', 'latitude': 27.91020012, 'longitude': -82.68740082, 'timezone': -5.0, 'dst': 'A', 'tz_id': 'America/New_York', 'type': 'airport', 'source': 'OurAirports'}, 'codeshare': False, 'stops': 0, 'equipment': ['M80', '320']}
{'airline': {'airline_id': 35, 'name': 'Allegiant Air', 'alias': '\\N', 'iata': 'G4', 'icao': 'AAY', 'callsign': 'ALLEGIANT', 'country': 'United St

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



{'airline': {'airline_id': 8745, 'name': 'Transavia France', 'alias': 'nan', 'iata': 'TO', 'icao': 'TVF', 'callsign': 'FRENCH SUN', 'country': 'France', 'active': True}, 'src_airport': {'airport_id': 293, 'name': 'Djerba Zarzis International Airport', 'city': 'Djerba', 'iata': 'DJE', 'icao': 'DTTJ', 'latitude': 33.875, 'longitude': 10.775500297546387, 'timezone': 1.0, 'dst': 'E', 'tz_id': 'Africa/Tunis', 'type': 'airport', 'source': 'OurAirports'}, 'dst_airport': {'airport_id': 1418, 'name': 'Nantes Atlantique Airport', 'city': 'Nantes', 'iata': 'NTE', 'icao': 'LFRS', 'latitude': 47.15319824220001, 'longitude': -1.61073005199, 'timezone': 1.0, 'dst': 'E', 'tz_id': 'Europe/Paris', 'type': 'airport', 'source': 'OurAirports'}, 'codeshare': False, 'stops': 0, 'equipment': ['73H']}
{'airline': {'airline_id': 8745, 'name': 'Transavia France', 'alias': 'nan', 'iata': 'TO', 'icao': 'TVF', 'callsign': 'FRENCH SUN', 'country': 'France', 'active': True}, 'src_airport': {'airport_id': 293, 'name':

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [24]:
from fastavro import parse_schema
parsed_schema = parse_schema(schema)
# parsed_schema

In [19]:
from fastavro import writer
with open(data_path, 'wb') as out:
    writer(out, parsed_schema, records)

In [29]:
from fastavro import parse_schema
from fastavro import writer

def create_avro_dataset(records):
    schema_path = schema_dir.joinpath('routes.avsc')
    data_path = results_dir.joinpath('routes.avro')
    
    ## TODO: Use fastavro to create Avro dataset
    
    # load schema .avro file
    with open(schema_path,'r') as f:
        schema = json.load(f)
    # parse schema
    parsed_schema = parse_schema(schema)
    # write record according to schema
    with open(data_path, 'wb') as out:
        writer(out, parsed_schema, records)

        
create_avro_dataset(records)

Make sure data reads back:

In [40]:
# from fastavro import reader
# with open(data_path, 'rb') as fo:
#     avro_reader = reader(fo)
#     for record in avro_reader:
#         print(record)

### 3.1.c Parquet

Create a Parquet dataset in `results/routes.parquet` using [Apache Arrow](https://arrow.apache.org/docs/python/).

In [41]:
src_data_path = 'data/processed/openflights/routes.jsonl.gz'
parquet_output_path = results_dir.joinpath('routes.parquet')
s3 = s3fs.S3FileSystem(
    anon=True,
    client_kwargs={
        'endpoint_url': endpoint_url
    }
)

In [45]:
with s3.open(src_data_path, 'rb') as f_gz:
    with gzip.open(f_gz, 'rb') as f:
#         for i in f:
#             print(i)
        table = read_json(f)

In [48]:
table.to_pandas().head()

airline  \
0  {'airline_id': 410, 'name': 'Aerocondor', 'ali...   
1  {'airline_id': 410, 'name': 'Aerocondor', 'ali...   
2  {'airline_id': 410, 'name': 'Aerocondor', 'ali...   
3  {'airline_id': 410, 'name': 'Aerocondor', 'ali...   
4  {'airline_id': 410, 'name': 'Aerocondor', 'ali...   

                                         src_airport  \
0  {'airport_id': 2965.0, 'name': 'Sochi Internat...   
1  {'airport_id': 2966.0, 'name': 'Astrakhan Airp...   
2  {'airport_id': 2966.0, 'name': 'Astrakhan Airp...   
3  {'airport_id': 2968.0, 'name': 'Chelyabinsk Ba...   
4  {'airport_id': 2968.0, 'name': 'Chelyabinsk Ba...   

                                         dst_airport  codeshare equipment  
0  {'airport_id': 2990.0, 'name': 'Kazan Internat...      False     [CR2]  
1  {'airport_id': 2990.0, 'name': 'Kazan Internat...      False     [CR2]  
2  {'airport_id': 2962.0, 'name': 'Mineralnyye Vo...      False     [CR2]  
3  {'airport_id': 2990.0, 'name': 'Kazan Internat...      False     [CR2]  
4  {'airport_id': 4078.0, 'name': 'Tolmachevo Air...      False     [CR2]

In [49]:
pq.write_table(table, parquet_output_path)

In [50]:
def create_parquet_dataset():
    src_data_path = 'data/processed/openflights/routes.jsonl.gz'
    parquet_output_path = results_dir.joinpath('routes.parquet')
    s3 = s3fs.S3FileSystem(
        anon=True,
        client_kwargs={
            'endpoint_url': endpoint_url
        }
    )
    
    with s3.open(src_data_path, 'rb') as f_gz:
        with gzip.open(f_gz, 'rb') as f:
#             pass
            ## TODO: Use Apache Arrow to create Parquet table and save the dataset
            table = read_json(f)
#     table.to_pandas()
    pq.write_table(table, parquet_output_path)
create_parquet_dataset()

LATER: Maybe put a pq.read_table() step in to verify

### 3.1.d Protocol Buffers

Using the generated code found in `sc650/assignment/assignment03/routes_pb2.py` create `results/routes.pb` using Protocol Buffers.

In [75]:
sys.path.insert(0, os.path.abspath('routes_pb2'))

import routes_pb2

def _airport_to_proto_obj(airport):
    obj = routes_pb2.Airport()
    if airport is None:
        return None
    if airport.get('airport_id') is None:
        return None

    obj.airport_id = airport.get('airport_id')
    if airport.get('name'):
        obj.name = airport.get('name')
    if airport.get('city'):
        obj.city = airport.get('city')
    if airport.get('iata'):
        obj.iata = airport.get('iata')
    if airport.get('icao'):
        obj.icao = airport.get('icao')
    if airport.get('altitude'):
        obj.altitude = airport.get('altitude')
    if airport.get('timezone'):
        obj.timezone = airport.get('timezone')
    if airport.get('dst'):
        obj.dst = airport.get('dst')
    if airport.get('tz_id'):
        obj.tz_id = airport.get('tz_id')
    if airport.get('type'):
        obj.type = airport.get('type')
    if airport.get('source'):
        obj.source = airport.get('source')

    obj.latitude = airport.get('latitude')
    obj.longitude = airport.get('longitude')

    return obj


def _airline_to_proto_obj(airline):
    obj = routes_pb2.Airline()
    ## TODO: Create an Airline obj using Protocol Buffers API
    if airline is None:
        return None
    if airline.get('airline_id') is None:
        return None
    
    obj.airline_id = airline.get('airline_id')
    if airline.get('name'):
        obj.name = airline.get('name')
    if airline.get('alias'):
        obj.alias = airline.get('alias')
    if airline.get('iata'):
        obj.iata = airline.get('iata')
    if airline.get('icao'):
        obj.icao = airline.get('icao')
    if airline.get('callsign'):
        obj.callsign = airline.get('callsign')
    if airline.get('country'):
        obj.country = airline.get('country')
    if airline.get('active'):
        obj.active = airline.get('active')  
        
    return obj


def create_protobuf_dataset(records):
    routes = routes_pb2.Routes()
    for record in records:
        route = routes_pb2.Route()
        ## TODO: Implement the code to create the Protocol Buffers Dataset
#         airline = _airline_to_proto_obj()
#         airport = _airport_to_proto_obj()
        routes.route.append(route)

    data_path = results_dir.joinpath('routes.pb')

    with open(data_path, 'wb') as f:
        f.write(routes.SerializeToString())
        
    compressed_path = results_dir.joinpath('routes.pb.snappy')
    
    with open(compressed_path, 'wb') as f:
        f.write(snappy.compress(routes.SerializeToString()))
        
# create_protobuf_dataset(records)

In [83]:
record = records[0]
record

{'airline': {'airline_id': 410,
  'name': 'Aerocondor',
  'alias': 'ANA All Nippon Airways',
  'iata': '2B',
  'icao': 'ARD',
  'callsign': 'AEROCONDOR',
  'country': 'Portugal',
  'active': True},
 'src_airport': {'airport_id': 2965,
  'name': 'Sochi International Airport',
  'city': 'Sochi',
  'country': 'Russia',
  'iata': 'AER',
  'icao': 'URSS',
  'latitude': 43.449902,
  'longitude': 39.9566,
  'altitude': 89,
  'timezone': 3.0,
  'dst': 'N',
  'tz_id': 'Europe/Moscow',
  'type': 'airport',
  'source': 'OurAirports'},
 'dst_airport': {'airport_id': 2990,
  'name': 'Kazan International Airport',
  'city': 'Kazan',
  'country': 'Russia',
  'iata': 'KZN',
  'icao': 'UWKD',
  'latitude': 55.606201171875,
  'longitude': 49.278701782227,
  'altitude': 411,
  'timezone': 3.0,
  'dst': 'N',
  'tz_id': 'Europe/Moscow',
  'type': 'airport',
  'source': 'OurAirports'},
 'codeshare': False,
 'equipment': ['CR2']}

In [133]:
route = routes_pb2.Route()

In [134]:
route

In [82]:
airline = _airline_to_proto_obj(record.get('airline'))
airline

airline_id: 410
name: "Aerocondor"
alias: "ANA All Nippon Airways"
iata: "2B"
icao: "ARD"
callsign: "AEROCONDOR"
country: "Portugal"
active: true

In [96]:
parts = set()
for record in records:
    for item in record:
        parts.add(item)

In [97]:
parts

{'airline', 'codeshare', 'dst_airport', 'equipment', 'src_airport'}

In [85]:
if airline:
    route.airline.CopyFrom(airline)

# src_airport
# dst_airport
# codeshare
# equipment

In [84]:
src_airport = _airport_to_proto_obj(record.get('src_airport'))
src_airport

airport_id: 2965
name: "Sochi International Airport"
city: "Sochi"
iata: "AER"
icao: "URSS"
latitude: 43.449902
longitude: 39.9566
altitude: 89
timezone: 3.0
dst: "N"
tz_id: "Europe/Moscow"
type: "airport"
source: "OurAirports"

In [86]:
if src_airport:
    route.src_airport.CopyFrom(src_airport)

In [87]:
dst_airport = _airport_to_proto_obj(record.get('dst_airport'))
dst_airport

airport_id: 2990
name: "Kazan International Airport"
city: "Kazan"
iata: "KZN"
icao: "UWKD"
latitude: 55.606201171875
longitude: 49.278701782227
altitude: 411
timezone: 3.0
dst: "N"
tz_id: "Europe/Moscow"
type: "airport"
source: "OurAirports"

In [88]:
if dst_airport:
    route.dst_airport.CopyFrom(dst_airport)

In [90]:
record.get('codeshare')

False

In [101]:
route.codeshare = record.get('codeshare')

In [102]:
route.codeshare

False

In [104]:
record.get('equipment')

['CR2']

In [112]:
n = 0
for i in records:
    print(f'{n}: {i.get("equipment")}')
    n += 1

0: ['CR2']
1: ['CR2']
2: ['CR2']
3: ['CR2']
4: ['CR2']
5: ['CR2']
6: ['CR2']
7: ['CR2']
8: ['CR2']
9: ['CR2']
10: ['CR2']
11: ['CR2']
12: ['CR2']
13: ['CR2']
14: ['CR2']
15: ['CR2']
16: ['CR2']
17: ['CR2']
18: ['CR2']
19: ['CR2']
20: ['CR2']
21: ['CR2']
22: ['CR2']
23: ['CR2']
24: ['CR2']
25: ['CR2']
26: ['CR2']
27: ['CR2']
28: ['CR2']
29: ['CR2']
30: ['CR2']
31: ['CR2']
32: ['CR2']
33: ['CR2']
34: ['CR2']
35: ['CR2']
36: ['CR2']
37: ['CR2']
38: ['CR2']
39: ['CR2']
40: ['CR2']
41: ['CR2']
42: ['A81']
43: ['A81']
44: ['A81']
45: ['AN4']
46: ['A81']
47: ['AN4']
48: ['AN4']
49: ['AN4']
50: ['A81']
51: ['AN4']
52: ['AN4']
53: ['A81']
54: ['AN4']
55: ['A81']
56: ['AN4']
57: ['A81']
58: ['A81']
59: ['A81']
60: ['AN4']
61: ['AN4']
62: ['A81']
63: ['142']
64: ['142', '141']
65: ['142']
66: ['141']
67: ['143']
68: ['142']
69: ['142']
70: ['142', '141']
71: ['141']
72: ['143', '146']
73: ['142', '146']
74: ['143']
75: ['143', '146']
76: ['146']
77: ['142']
78: ['142']
79: ['142', '146']
80: ['14

2882: ['BNI']
2883: ['DHT']
2884: ['F50']
2885: ['CR2']
2886: ['CR2']
2887: ['CR2']
2888: ['CR2']
2889: ['CR2']
2890: ['CR2']
2891: ['CR2']
2892: ['CR2']
2893: ['CR2']
2894: ['CR2']
2895: ['CR2']
2896: ['CR2']
2897: ['CR2']
2898: ['CR2']
2899: ['CR2']
2900: ['CR2']
2901: ['CR2']
2902: ['CR2']
2903: ['CR2']
2904: ['CR2']
2905: ['CR2']
2906: ['CR2']
2907: ['CR2']
2908: ['CR2']
2909: ['EM2']
2910: ['CR2']
2911: ['CR2']
2912: ['CR2']
2913: ['CR2']
2914: ['CR2']
2915: ['CR2']
2916: ['CR2']
2917: ['CR2']
2918: ['CR2']
2919: ['CR2']
2920: ['CR2']
2921: ['CR2']
2922: ['CR2']
2923: ['CR2']
2924: ['EM2']
2925: ['CR2']
2926: ['CR2']
2927: ['CR2']
2928: ['CR2']
2929: ['CR2']
2930: ['CR2']
2931: ['CR2']
2932: ['CR2']
2933: ['CR2']
2934: ['CR2']
2935: ['CR2']
2936: ['EM2']
2937: ['CR2']
2938: ['EM2']
2939: ['CR2']
2940: ['CR2']
2941: ['CR2']
2942: ['EM2']
2943: ['CR2']
2944: ['EM2']
2945: ['EM2']
2946: ['CR2']
2947: ['CR2']
2948: ['EM2']
2949: ['CR2']
2950: ['CR2']
2951: ['CR2']
2952: ['CR2']
2953: 

5617: ['330']
5618: ['773']
5619: ['ER4']
5620: ['738']
5621: ['32B', '762']
5622: ['318']
5623: ['777', '77W']
5624: ['763']
5625: ['330', '757', '340']
5626: ['757']
5627: ['763', '757']
5628: ['757', '763', '738']
5629: ['763']
5630: ['787', '773']
5631: ['738']
5632: ['ER4']
5633: ['757']
5634: ['763']
5635: ['321']
5636: ['ER4']
5637: ['ERD', 'CR7']
5638: ['738']
5639: ['787']
5640: ['738']
5641: ['32B', '763']
5642: ['738']
5643: ['757']
5644: ['757']
5645: ['757']
5646: ['CR7']
5647: ['330']
5648: ['ERD']
5649: ['737']
5650: ['CR7']
5651: ['763']
5652: ['ER4']
5653: ['380', '744']
5654: ['737']
5655: ['320']
5656: ['763']
5657: ['738']
5658: ['777']
5659: ['757']
5660: ['737']
5661: ['757']
5662: ['737']
5663: ['734']
5664: ['734']
5665: ['737']
5666: ['380']
5667: ['777']
5668: ['737']
5669: ['380']
5670: ['763']
5671: ['737']
5672: ['737']
5673: ['744']
5674: ['321']
5675: ['320', '319']
5676: ['M80', '738', 'M83', '757']
5677: ['738']
5678: ['738']
5679: ['777']
5680: ['744']

8435: ['763']
8436: ['319']
8437: ['319']
8438: ['CRJ']
8439: ['319']
8440: ['BEH']
8441: ['319']
8442: ['E90']
8443: ['CRJ']
8444: ['CRA', 'CRJ']
8445: ['CRA']
8446: ['77W']
8447: ['319']
8448: ['77W']
8449: ['E75']
8450: ['77W']
8451: ['E75']
8452: ['319']
8453: ['DH1']
8454: ['E90']
8455: ['319']
8456: ['319']
8457: ['77L']
8458: ['CRJ']
8459: ['BEH']
8460: ['320']
8461: ['319']
8462: ['763']
8463: ['E90']
8464: ['320']
8465: ['319']
8466: ['319']
8467: ['CRJ']
8468: ['BEH']
8469: ['763']
8470: ['319']
8471: ['319']
8472: ['763']
8473: ['319']
8474: ['788']
8475: ['DH1']
8476: ['E90']
8477: ['320', '319', 'E90']
8478: ['DH4']
8479: ['BEH']
8480: ['320', 'E90', '319', '763']
8481: ['E90', '320', '319']
8482: ['E90', '319', '320', '763', 'E75']
8483: ['DH4']
8484: ['319']
8485: ['DH4', 'CRJ']
8486: ['E90']
8487: ['DH4', 'CRJ']
8488: ['CRJ']
8489: ['DH1']
8490: ['DH4']
8491: ['DH1']
8492: ['319', '321', '320', 'E90', '333', '763', 'E75']
8493: ['321', '320', '77W', '763', '77L', '319',

12185: ['763']
12186: ['738']
12187: ['738']
12188: ['738']
12189: ['738']
12190: ['738']
12191: ['738']
12192: ['73G']
12193: ['738', 'AT7']
12194: ['738']
12195: ['AT7']
12196: ['AT7']
12197: ['738']
12198: ['738']
12199: ['738', '73G']
12200: ['738']
12201: ['AT7']
12202: ['738']
12203: ['738']
12204: ['73G']
12205: ['738']
12206: ['738', '73G']
12207: ['738']
12208: ['738']
12209: ['738']
12210: ['738']
12211: ['738']
12212: ['738', 'AT7']
12213: ['738']
12214: ['738', '73G']
12215: ['738']
12216: ['738', '73G']
12217: ['738']
12218: ['738']
12219: ['73G', '738']
12220: ['738']
12221: ['738']
12222: ['738', '763']
12223: ['738']
12224: ['738']
12225: ['738']
12226: ['738']
12227: ['738', '744']
12228: ['738']
12229: ['738', '73G']
12230: ['738']
12231: ['738']
12232: ['73G']
12233: ['73G', 'AT7', '738']
12234: ['738']
12235: ['738']
12236: ['738']
12237: ['73G']
12238: ['738', 'AT7']
12239: ['738']
12240: ['738']
12241: ['738']
12242: ['738']
12243: ['73G', '738']
12244: ['738']
12

...

53250: ['73H']
53251: ['73H']
53252: ['73H']
53253: ['73H']
53254: ['73H']
53255: ['73H']
53256: ['73H']
53257: ['73H']
53258: ['73H']
53259: ['73H']
53260: ['75W']
53261: ['73H']
53262: ['75W', '73H']
53263: ['73H', '75W', '76W']
53264: ['76W', '73H']
53265: ['73H', '76W']
53266: ['75W']
53267: ['73H', '76W']
53268: ['75W']
53269: ['788', '76W']
53270: ['73H']
53271: ['76W', '73H', '75W']
53272: ['73H']
53273: ['75W']
53274: ['73H']
53275: ['73H']
53276: ['73H']
53277: ['73H', '75W', '76W']
53278: ['75W']
53279: ['73H']
53280: ['73H']
53281: ['73H']
53282: ['73H']
53283: ['73H']
53284: ['73H']
53285: ['73H']
53286: ['73H', '76W']
53287: ['73H', '75W']
53288: ['788']
53289: ['73H']
53290: ['73H']
53291: ['73H']
53292: ['73H', '75W']
53293: ['76W']
53294: ['75W']
53295: ['75W']
53296: ['73H']
53297: ['73H']
53298: ['75W']
53299: ['73H']
53300: ['73H']
53301: ['73H']
53302: ['73H']
53303: ['73H']
53304: ['73H']
53305: ['73H']
53306: ['788']
53307: ['75W', '73H']
53308: ['73H']
53309: ['7

56567: ['CRJ']
56568: ['763']
56569: ['777']
56570: ['763']
56571: ['752']
56572: ['764']
56573: ['777']
56574: ['763']
56575: ['764']
56576: ['764']
56577: ['738', '753', '777', '739']
56578: ['AT7']
56579: ['738']
56580: ['744']
56581: ['AT7']
56582: ['777']
56583: ['330']
56584: ['764', '777', '738', '753', '739']
56585: ['ERJ']
56586: ['BE1']
56587: ['ERJ']
56588: ['ERJ', 'CRJ']
56589: ['ERJ']
56590: ['ERJ', 'CRJ']
56591: ['ERJ']
56592: ['ERJ']
56593: ['ERJ']
56594: ['DH4', 'DH2', 'CR7', 'CRJ', 'ERJ']
56595: ['763']
56596: ['SF3']
56597: ['CR7', 'CRJ', 'ERJ', 'E70']
56598: ['739']
56599: ['319']
56600: ['738', '319', '320']
56601: ['DH2']
56602: ['SF3']
56603: ['ERJ', 'CRJ']
56604: ['319']
56605: ['320', '752', '73G', '739', '738']
56606: ['777', '332']
56607: ['CRJ', 'DH4', 'CR7', 'ERJ', 'ER4']
56608: ['DH4', 'ERJ', 'DH2', 'E70', 'CRJ', 'CR7', 'ER4']
56609: ['CRJ']
56610: ['763']
56611: ['DH2']
56612: ['CRJ']
56613: ['DH4']
56614: ['CR7', 'ERJ']
56615: ['DH4', 'ERJ', 'CR7', 'ER4',

59899: ['ERD', 'ER4']
59900: ['ERD', 'ER4', 'E75']
59901: ['763']
59902: ['763']
59903: ['E75']
59904: ['ER4', 'ERD']
59905: ['CR7', 'E75']
59906: ['ER4']
59907: ['763']
59908: ['738']
59909: ['ER4', 'ERD']
59910: ['ERD']
59911: ['ERD', 'ER4']
59912: ['ER4']
59913: ['ER4', 'ERD']
59914: ['ERD']
59915: ['ER4']
59916: ['CR7']
59917: ['CRJ']
59918: ['ER4', 'ERD', 'E75', 'CR7']
59919: ['330']
59920: ['ER4', 'CR7']
59921: ['738']
59922: ['738', 'M83']
59923: ['738']
59924: ['ERD', 'ER4']
59925: ['738']
59926: ['763', '777']
59927: ['ER4']
59928: ['ER4', 'ERD']
59929: ['763']
59930: ['738']
59931: ['CR7', 'ER4']
59932: ['738', 'M83', 'M80']
59933: ['ERD', 'CR7']
59934: ['CR7']
59935: ['738']
59936: ['ERD', 'ER4']
59937: ['738', '763']
59938: ['CRJ']
59939: ['ERD', 'ER4']
59940: ['ER4']
59941: ['ER4', 'ERD']
59942: ['E75']
59943: ['E75']
59944: ['777']
59945: ['ER4']
59946: ['CR7']
59947: ['M83', 'M80']
59948: ['738']
59949: ['777']
59950: ['320', '321', '319', 'E90']
59951: ['321', '738', 'M

62884: ['320']
62885: ['320']
62886: ['320']
62887: ['320']
62888: ['320']
62889: ['320']
62890: ['320']
62891: ['320']
62892: ['320']
62893: ['320']
62894: ['320']
62895: ['320']
62896: ['320']
62897: ['320']
62898: ['320']
62899: ['320']
62900: ['320']
62901: ['320']
62902: ['320']
62903: ['320']
62904: ['320']
62905: ['320']
62906: ['320']
62907: ['320']
62908: ['320']
62909: ['320']
62910: ['320']
62911: ['320']
62912: ['320']
62913: ['320']
62914: ['320']
62915: ['320']
62916: ['320']
62917: ['320']
62918: ['320']
62919: ['320']
62920: ['320']
62921: ['320']
62922: ['320']
62923: ['320']
62924: ['320']
62925: ['320']
62926: ['320']
62927: ['320']
62928: ['320']
62929: ['320']
62930: ['320']
62931: ['320']
62932: ['320']
62933: ['320']
62934: ['320']
62935: ['320']
62936: ['320']
62937: ['320']
62938: ['320']
62939: ['320']
62940: ['320']
62941: ['320']
62942: ['320']
62943: ['320']
62944: ['320']
62945: ['320']
62946: ['320']
62947: ['320']
62948: ['320']
62949: ['320']
62950: ['3

66208: ['DH8']
66209: ['DH8']
66210: ['DH8']
66211: ['DH8']
66212: ['DH8']
66213: ['DH1']
66214: ['DH1', 'BEC']
66215: ['DH8']
66216: ['DH8']
66217: ['DH8']
66218: ['BET']
66219: ['DH8']
66220: ['DH8']
66221: ['DH8']
66222: ['DH1']
66223: ['DH1']
66224: ['320']
66225: ['320']
66226: ['NDE']
66227: ['NDE']
66228: ['SFB']
66229: ['S20']
66230: ['SFB']
66231: ['S20']
66232: ['S20']
66233: ['S20']
66234: ['S20']
66235: ['S20']
66236: ['S20']
66237: ['S20']
66238: ['S20']
66239: ['S20']
66240: ['S20']
66241: ['S20']
66242: ['CNA']
66243: ['CNA']
66244: ['J41']
66245: ['J41']
66246: ['J41']
66247: ['J41']
66248: ['J41']
66249: ['J41']
66250: ['J41']
66251: ['J41']
66252: ['J41']
66253: ['J41']
66254: ['J41']
66255: ['J41']
66256: ['J41']
66257: ['J41']
66258: ['J41']
66259: ['J41']
66260: ['J41']
66261: ['J41']
66262: ['320']
66263: ['320']
66264: ['320']
66265: ['319', '320']
66266: ['320']
66267: ['320']
66268: ['320']
66269: ['320']
66270: ['320', '319']
66271: ['320']
66272: ['320']
6627

In [113]:
records[82].get('equipment')

['E70', 'CRJ', 'M87']

In [136]:
record = records[82]

In [139]:
equipment = record.get('equipment')
equipment

['E70', 'CRJ', 'M87']

In [140]:
route.equipment.CopyFrom(equiment)

AttributeError: 'google.protobuf.pyext._message.RepeatedScalarConta' object has no attribute 'CopyFrom'

In [128]:
route.equipment = record.get('equipment')

AttributeError: Assignment not allowed to repeated field "equipment" in protocol message object.

In [118]:
for i, v in enumerate(equipment):
    print(i)
    print(v)

0
E70
1
CRJ
2
M87


In [130]:
for i in equipment:
    route.equipment.append(i)

In [131]:
route

equipment: "E70"
equipment: "CRJ"
equipment: "M87"

In [125]:
route.Clear()

In [126]:
route

In [143]:
def _airport_to_proto_obj(airport):
    obj = routes_pb2.Airport()
    if airport is None:
        return None
    if airport.get('airport_id') is None:
        return None

    obj.airport_id = airport.get('airport_id')
    if airport.get('name'):
        obj.name = airport.get('name')
    if airport.get('city'):
        obj.city = airport.get('city')
    if airport.get('iata'):
        obj.iata = airport.get('iata')
    if airport.get('icao'):
        obj.icao = airport.get('icao')
    if airport.get('altitude'):
        obj.altitude = airport.get('altitude')
    if airport.get('timezone'):
        obj.timezone = airport.get('timezone')
    if airport.get('dst'):
        obj.dst = airport.get('dst')
    if airport.get('tz_id'):
        obj.tz_id = airport.get('tz_id')
    if airport.get('type'):
        obj.type = airport.get('type')
    if airport.get('source'):
        obj.source = airport.get('source')

    obj.latitude = airport.get('latitude')
    obj.longitude = airport.get('longitude')

    return obj

In [153]:
def _airline_to_proto_obj(airline):
    obj = routes_pb2.Airline()
    ## TODO: Create an Airline obj using Protocol Buffers API
    if airline is None:
        return None
    if airline.get('airline_id') is None:
        return None
    
    obj.airline_id = airline.get('airline_id')
    if airline.get('name'):
        obj.name = airline.get('name')
    if airline.get('alias'):
        obj.alias = airline.get('alias')
    if airline.get('iata'):
        obj.iata = airline.get('iata')
    if airline.get('icao'):
        obj.icao = airline.get('icao')
    if airline.get('callsign'):
        obj.callsign = airline.get('callsign')
    if airline.get('country'):
        obj.country = airline.get('country')
    obj.active = airline.get('active')  
        
    return obj

In [146]:
def create_protobuf_dataset(records):
    routes = routes_pb2.Routes()
    for record in records:
        route = routes_pb2.Route()
        
        ## TODO: Implement the code to create the Protocol Buffers Dataset
        # Copy 'airline' data
        airline = _airline_to_proto_obj(record.get('airline'))
        if airline:
            route.airline.CopyFrom(airline)
        
        # Copy 'src_airport' data
        src_airport = _airport_to_proto_obj(record.get('src_airport'))
        if src_airport:
            route.src_airport.CopyFrom(src_airport)
        
        # Copy 'dst_airport' data
        dst_airport = _airport_to_proto_obj(record.get('dst_airport'))
        if dst_airport:
            route.dst_airport.CopyFrom(dst_airport)
        
        # Get 'codeshare' boolean
        route.codeshare = record.get('codeshare')
        
        # Get 'equipment' and iterate through for multiple
        equipment = record.get('equipment')
        for equip in equipment:
            route.equipment.append(equip)
        
        # Add generated route to db of routes
        routes.route.append(route)

    data_path = results_dir.joinpath('routes.pb')

    with open(data_path, 'wb') as f:
        f.write(routes.SerializeToString())
        
    compressed_path = results_dir.joinpath('routes.pb.snappy')
    
    with open(compressed_path, 'wb') as f:
        f.write(snappy.compress(routes.SerializeToString()))

In [152]:
records[63]

{'airline': {'airline_id': 8359,
  'name': 'Star Peru (2I)',
  'alias': 'nan',
  'iata': '2I',
  'icao': 'FOF',
  'callsign': 'nan',
  'country': 'Peru',
  'active': True},
 'src_airport': {'airport_id': 2786,
  'name': 'Coronel FAP Alfredo Mendivil Duarte Airport',
  'city': 'Ayacucho',
  'country': 'Peru',
  'iata': 'AYP',
  'icao': 'SPHO',
  'latitude': -13.154800415039062,
  'longitude': -74.20439910888672,
  'altitude': 8917,
  'timezone': -5.0,
  'dst': 'U',
  'tz_id': 'America/Lima',
  'type': 'airport',
  'source': 'OurAirports'},
 'dst_airport': {'airport_id': 2789,
  'name': 'Jorge Chávez International Airport',
  'city': 'Lima',
  'country': 'Peru',
  'iata': 'LIM',
  'icao': 'SPIM',
  'latitude': -12.0219,
  'longitude': -77.114305,
  'altitude': 113,
  'timezone': -5.0,
  'dst': 'U',
  'tz_id': 'America/Lima',
  'type': 'airport',
  'source': 'OurAirports'},
 'codeshare': False,
 'equipment': ['142']}

In [154]:
create_protobuf_dataset(records)

In [56]:
routes = routes_pb2.Routes()

## 3.2

### 3.2.a Simple Geohash Index

In [ ]:
def create_hash_dirs(records):
    geoindex_dir = results_dir.joinpath('geoindex')
    geoindex_dir.mkdir(exist_ok=True, parents=True)
    hashes = []
    ## TODO: Create hash index
            
create_hash_dirs(records)

In [3]:
geoindex_dir = results_dir.joinpath('geoindex')
geoindex_dir

PosixPath('/home/jovyan/dsc650/dsc650/assignments/assignment03/results/geoindex')

In [4]:
geoindex_dir.mkdir(exist_ok=True, parents=True)

In [5]:
hashes = []

In [6]:
pygeohash.encode(41.1499988, -95.91779) # Bellevue

'9z7f174u17zb'

In [7]:
pygeohash.encode(40.787560, -96.743690) # My house

'9z70n91ku8k2'

In [8]:
pygeohash.geohash_approximate_distance('9z7f174u17zb', '9z70n91ku8k2')

123264

In [12]:
records[0]

{'airline': {'airline_id': 410,
  'name': 'Aerocondor',
  'alias': 'ANA All Nippon Airways',
  'iata': '2B',
  'icao': 'ARD',
  'callsign': 'AEROCONDOR',
  'country': 'Portugal',
  'active': True},
 'src_airport': {'airport_id': 2965,
  'name': 'Sochi International Airport',
  'city': 'Sochi',
  'country': 'Russia',
  'iata': 'AER',
  'icao': 'URSS',
  'latitude': 43.449902,
  'longitude': 39.9566,
  'altitude': 89,
  'timezone': 3.0,
  'dst': 'N',
  'tz_id': 'Europe/Moscow',
  'type': 'airport',
  'source': 'OurAirports'},
 'dst_airport': {'airport_id': 2990,
  'name': 'Kazan International Airport',
  'city': 'Kazan',
  'country': 'Russia',
  'iata': 'KZN',
  'icao': 'UWKD',
  'latitude': 55.606201171875,
  'longitude': 49.278701782227,
  'altitude': 411,
  'timezone': 3.0,
  'dst': 'N',
  'tz_id': 'Europe/Moscow',
  'type': 'airport',
  'source': 'OurAirports'},
 'codeshare': False,
 'equipment': ['CR2']}

In [17]:
records[0]['src_airport']

{'airport_id': 2965,
 'name': 'Sochi International Airport',
 'city': 'Sochi',
 'country': 'Russia',
 'iata': 'AER',
 'icao': 'URSS',
 'latitude': 43.449902,
 'longitude': 39.9566,
 'altitude': 89,
 'timezone': 3.0,
 'dst': 'N',
 'tz_id': 'Europe/Moscow',
 'type': 'airport',
 'source': 'OurAirports'}

In [20]:
lat = records[0]['src_airport']['latitude']
lat

43.449902

In [21]:
lon = records[0]['src_airport']['longitude']
lon

39.9566

In [22]:
pygeohash.encode(lat, lon)

'szsrjjzd02b3'

In [43]:
record = records[0]

In [26]:
record['src_airport']

{'airport_id': 2965,
 'name': 'Sochi International Airport',
 'city': 'Sochi',
 'country': 'Russia',
 'iata': 'AER',
 'icao': 'URSS',
 'latitude': 43.449902,
 'longitude': 39.9566,
 'altitude': 89,
 'timezone': 3.0,
 'dst': 'N',
 'tz_id': 'Europe/Moscow',
 'type': 'airport',
 'source': 'OurAirports'}

In [25]:
record['src_airport'].get('name')

'Sochi International Airport'

In [28]:
record.get('src_airport', {})

{'airport_id': 2965,
 'name': 'Sochi International Airport',
 'city': 'Sochi',
 'country': 'Russia',
 'iata': 'AER',
 'icao': 'URSS',
 'latitude': 43.449902,
 'longitude': 39.9566,
 'altitude': 89,
 'timezone': 3.0,
 'dst': 'N',
 'tz_id': 'Europe/Moscow',
 'type': 'airport',
 'source': 'OurAirports'}

In [44]:
origin_data = record.get('src_airport')
origin_data

{'airport_id': 2965,
 'name': 'Sochi International Airport',
 'city': 'Sochi',
 'country': 'Russia',
 'iata': 'AER',
 'icao': 'URSS',
 'latitude': 43.449902,
 'longitude': 39.9566,
 'altitude': 89,
 'timezone': 3.0,
 'dst': 'N',
 'tz_id': 'Europe/Moscow',
 'type': 'airport',
 'source': 'OurAirports'}

In [33]:
lat_lon = origin_data.get('latitude'), origin_data.get('longitude')
lat_lon

(43.449902, 39.9566)

In [35]:
pygeohash.encode(lat_lon[0], lat_lon[1])

'szsrjjzd02b3'

In [36]:
pygeohash.encode(43.449902, 39.9566)

'szsrjjzd02b3'

In [52]:
pygeohash.encode(41.79572812575813, -87.75424003142952)

'dp3tg0emf02j'

In [53]:
pygeohash.encode(41.992511088717386, -87.90942191965955)

'dp3qzsd2452j'

In [37]:
pygeohash.decode('szs')

(43.0, 40.0)

In [86]:
origin_data

{'airport_id': 2913,
 'name': 'Osh Airport',
 'city': 'Osh',
 'country': 'Kyrgyzstan',
 'iata': 'OSS',
 'icao': 'UAFO',
 'latitude': 40.6090011597,
 'longitude': 72.793296814,
 'altitude': 2927,
 'timezone': 6.0,
 'dst': 'U',
 'tz_id': 'Asia/Bishkek',
 'type': 'airport',
 'source': 'OurAirports'}

In [87]:
x, y = origin_data.get('latitude'), origin_data.get('longitude')

In [88]:
x

40.6090011597

In [89]:
y

72.793296814

In [142]:
# georecords = records.copy()

In [155]:
geo_records = read_jsonl_data()

hashes, hash_set = [], set()
for record in geo_records:
    origin_data = record.get('src_airport')
    if origin_data:
        lat, lon = origin_data.get('latitude'), origin_data.get('longitude')
        hash_set.add(pygeohash.encode(lat, lon, precision=3))
        record['src_airport']['geohash'] = pygeohash.encode(lat, lon)

hashes = sorted(list(hash_set))
# hashes

In [157]:
# origin_data

In [162]:
index = {value: [] for value in hashes}
index

{'2eg': [],
 '2ev': [],
 '2ey': [],
 '2h5': [],
 '2hb': [],
 '2hx': [],
 '2j0': [],
 '2j3': [],
 '2jd': [],
 '2jq': [],
 '2jt': [],
 '2kn': [],
 '2kp': [],
 '2kr': [],
 '2kw': [],
 '2s2': [],
 '2sh': [],
 '2sv': [],
 '2t5': [],
 '2th': [],
 '2tp': [],
 '2tq': [],
 '2tr': [],
 '2ug': [],
 '2v0': [],
 '2v1': [],
 '2v2': [],
 '2yk': [],
 '2ym': [],
 '35b': [],
 '3e4': [],
 '3zz': [],
 '4qr': [],
 '4qt': [],
 '4qy': [],
 '4rh': [],
 '4rv': [],
 '4wy': [],
 '4xb': [],
 '627': [],
 '62m': [],
 '62s': [],
 '62t': [],
 '62u': [],
 '62v': [],
 '63h': [],
 '63k': [],
 '63p': [],
 '63z': [],
 '66j': [],
 '66p': [],
 '66r': [],
 '66t': [],
 '67j': [],
 '67v': [],
 '683': [],
 '68e': [],
 '695': [],
 '696': [],
 '69r': [],
 '69y': [],
 '6cb': [],
 '6d0': [],
 '6d6': [],
 '6db': [],
 '6dc': [],
 '6dh': [],
 '6dk': [],
 '6dx': [],
 '6e1': [],
 '6e4': [],
 '6e9': [],
 '6en': [],
 '6eq': [],
 '6ex': [],
 '6f6': [],
 '6f9': [],
 '6fc': [],
 '6fe': [],
 '6ff': [],
 '6fg': [],
 '6fu': [],
 '6g0': [],
 '6g

In [161]:
record['src_airport'].get('geohash')

'tx5z02wkwf2p'

In [166]:
for record in geo_records:
    if record.get('src_airport'):
        geohash = record['src_airport'].get('geohash')
        index[geohash[:3]].append(record)

In [168]:
index['2eg']

[{'airline': {'airline_id': 692,
   'name': 'Air Tahiti',
   'alias': 'Pulkovo Aviation Enterprise',
   'iata': 'VT',
   'icao': 'VTA',
   'callsign': 'AIR TAHITI',
   'country': 'French Polynesia',
   'active': True},
  'src_airport': {'airport_id': 6926,
   'name': 'Rimatara Airport',
   'city': 'Rimatara',
   'country': 'French Polynesia',
   'iata': 'RMT',
   'icao': 'NTAM',
   'latitude': -22.63725,
   'longitude': -152.8059,
   'altitude': 60,
   'timezone': -10.0,
   'dst': 'U',
   'tz_id': 'Asia/Irkutsk',
   'type': 'airport',
   'source': 'OurAirports',
   'geohash': '2egr4z40kqwx'},
  'dst_airport': {'airport_id': 4075,
   'name': "Faa'a International Airport",
   'city': 'Papeete',
   'country': 'French Polynesia',
   'iata': 'PPT',
   'icao': 'NTAA',
   'latitude': -17.553698999999998,
   'longitude': -149.60699499999998,
   'altitude': 5,
   'timezone': -10.0,
   'dst': 'U',
   'tz_id': 'Pacific/Tahiti',
   'type': 'airport',
   'source': 'OurAirports'},
  'codeshare': Fal

In [119]:
# index['2eg'].append(record)

In [173]:
index['2eg']

[{'airline': {'airline_id': 692,
   'name': 'Air Tahiti',
   'alias': 'Pulkovo Aviation Enterprise',
   'iata': 'VT',
   'icao': 'VTA',
   'callsign': 'AIR TAHITI',
   'country': 'French Polynesia',
   'active': True},
  'src_airport': {'airport_id': 6926,
   'name': 'Rimatara Airport',
   'city': 'Rimatara',
   'country': 'French Polynesia',
   'iata': 'RMT',
   'icao': 'NTAM',
   'latitude': -22.63725,
   'longitude': -152.8059,
   'altitude': 60,
   'timezone': -10.0,
   'dst': 'U',
   'tz_id': 'Asia/Irkutsk',
   'type': 'airport',
   'source': 'OurAirports',
   'geohash': '2egr4z40kqwx'},
  'dst_airport': {'airport_id': 4075,
   'name': "Faa'a International Airport",
   'city': 'Papeete',
   'country': 'French Polynesia',
   'iata': 'PPT',
   'icao': 'NTAA',
   'latitude': -17.553698999999998,
   'longitude': -149.60699499999998,
   'altitude': 5,
   'timezone': -10.0,
   'dst': 'U',
   'tz_id': 'Pacific/Tahiti',
   'type': 'airport',
   'source': 'OurAirports'},
  'codeshare': Fal

In [124]:
pygeohash.encode(43.0612983704, 74.4776000977)

'txsuyz0fjzgd'

In [125]:
test = record

In [130]:
test['geohash'] = 'txsuyz0fjzgd'

In [135]:
test['src_airport']['test'] = 'txsuyz0fjzgd'
# record['src_airport']['geohash'] = hash_val
# test

In [180]:
for key, values in index.items():
    print(key)

2eg
2ev
2ey
2h5
2hb
2hx
2j0
2j3
2jd
2jq
2jt
2kn
2kp
2kr
2kw
2s2
2sh
2sv
2t5
2th
2tp
2tq
2tr
2ug
2v0
2v1
2v2
2yk
2ym
35b
3e4
3zz
4qr
4qt
4qy
4rh
4rv
4wy
4xb
627
62m
62s
62t
62u
62v
63h
63k
63p
63z
66j
66p
66r
66t
67j
67v
683
68e
695
696
69r
69y
6cb
6d0
6d6
6db
6dc
6dh
6dk
6dx
6e1
6e4
6e9
6en
6eq
6ex
6f6
6f9
6fc
6fe
6ff
6fg
6fu
6g0
6g1
6g3
6g4
6g5
6g7
6g9
6gg
6gj
6gm
6gy
6gz
6kp
6kq
6kt
6ky
6mc
6me
6mj
6mp
6mq
6ms
6my
6nx
6nz
6pb
6pn
6pq
6pr
6px
6py
6q1
6q2
6q3
6q8
6qc
6qd
6qp
6qs
6qy
6r7
6r8
6rb
6rc
6rf
6rn
6rq
6ru
6ry
6s1
6s2
6s4
6s9
6sb
6sg
6sp
6sw
6t2
6t3
6tt
6tu
6u0
6u3
6u5
6ug
6uh
6uj
6uk
6um
6un
6ut
6uv
6uw
6v0
6v1
6vb
6vg
6vh
6vj
6vt
6vv
6vz
6w1
6w6
6wh
6x3
6x7
6xb
6xc
6xg
6xm
6xx
6y0
6yg
6yh
6yj
6ys
6yt
6yu
6z0
6z6
6z9
6zj
6zk
6zn
6zv
75c
75f
7h1
7h2
7h4
7h7
7h8
7h9
7hd
7j0
7j3
7j6
7j9
7jf
7jh
7jk
7js
7n7
7nj
7nk
7nq
7ns
7nw
7nx
7ny
7p1
7p8
7pk
7r2
87y
87z
882
8e8
8e9
8eb
9em
9ep
9eq
9er
9et
9ev
9ew
9ex
9ez
9fc
9ff
9fg
9fv
9fw
9fx
9g3
9g5
9g6
9g7
9g8
9gb
9gd
9gf
9gh
9gj
9gq
9gx


In [178]:
key = '2eg'
# str(key[:2])
output_dir = geoindex_dir.joinpath(str(key[:1])).joinpath(str(key[:2]))
output_dir.mkdir(exist_ok=True, parents=True)
output_path = output_dir.joinpath(f'{key}.jsonl.gz')


In [3]:
geo_records = read_jsonl_data()

def create_hash_dirs(records):
    geoindex_dir = results_dir.joinpath('geoindex')
    geoindex_dir.mkdir(exist_ok=True, parents=True)
#     hashes = []

    ## TODO: Create hash index
    hashes, hash_set = [], set()
    for record in records: # iterate records
        origin_data = record.get('src_airport') # get source airport info
        if origin_data: # if source airport available, get lat/lon
            lat, lon = origin_data.get('latitude'), origin_data.get('longitude')
            hash_set.add(pygeohash.encode(lat, lon, precision=3)) # get 3-digit unique hash
            record['src_airport']['geohash'] = pygeohash.encode(lat, lon) # add full hash to record

    hashes = sorted(list(hash_set)) # sort unique hashes
    index = {value: [] for value in hashes} # set up hash index
    
    for record in records: 
        # iterate through records, add to appropriate hash index
        if record.get('src_airport'):
            geohash = record['src_airport'].get('geohash')
            index[geohash[:3]].append(record)
    
    for key, values in index.items():
        # create folder / subfolder directories by short hash key
        output_dir = geoindex_dir.joinpath(str(key[:1])).joinpath(str(key[:2]))
        output_dir.mkdir(exist_ok=True, parents=True)
        output_path = output_dir.joinpath(f'{key}.jsonl.gz')
        # save record to appropriate subfolder/file
        with gzip.open(output_path, 'w') as f:
            json_output = '\n'.join([json.dumps(value) for value in values])
            f.write(json_output.encode('utf-8'))
            
create_hash_dirs(geo_records)

In [171]:
# origin_data = record.get('src_airport')
# lat = origin_data.get('latitude')
# lon = origin_data.get('longitude')
# hashes.append(pygeohash.encode(lat, lon))

In [172]:
# uniq_list = list(unique_hashes)
# uniq_list.sort()
# uniq_list

### 3.2.b Simple Search Feature

In [ ]:
def airport_search(latitude, longitude):
    ## TODO: Create simple search to return nearest airport
    pass
    
airport_search(41.1499988, -95.91779)

In [10]:
val = input("Enter info: ")
print(f'\n{val}')

Enter info: booze

booze


Enter your latitude: 41.1499988
Enter your longitude: -95.91779
Input search radius (km): 1000

In [30]:
def airport_search(latitude=41.1499988, longitude=-95.91779, distance=1000):
    print(f'Latitude:  {latitude}')
    print(f'Longitude: {longitude}')
    print(f'Distance:  {distance} km')
    ## TODO: Create simple search to return nearest airport
    homeHash = pygeohash.encode(latitude, longitude)
    print(f'Your Geohash is: {homeHash}')
    pass

In [33]:
lat = float(input("Enter your latitude:\t"))
lon = float(input("Enter your longitude:\t"))
dist = float(input("Input search radius (km): "))
# airport_search(lat, lon, dist)

Enter your latitude:	41.1499988
Enter your longitude:	-95.917790
Input search radius (km): 1000


In [34]:
type(lat)

float

In [35]:
airport_search(lat, lon, dist)

Latitude:  41.1499988
Longitude: -95.91779
Distance:  1000.0 km
Your Geohash is: 9z7f174u17zb


In [20]:
geo_records[0]

{'airline': {'airline_id': 410,
  'name': 'Aerocondor',
  'alias': 'ANA All Nippon Airways',
  'iata': '2B',
  'icao': 'ARD',
  'callsign': 'AEROCONDOR',
  'country': 'Portugal',
  'active': True},
 'src_airport': {'airport_id': 2965,
  'name': 'Sochi International Airport',
  'city': 'Sochi',
  'country': 'Russia',
  'iata': 'AER',
  'icao': 'URSS',
  'latitude': 43.449902,
  'longitude': 39.9566,
  'altitude': 89,
  'timezone': 3.0,
  'dst': 'N',
  'tz_id': 'Europe/Moscow',
  'type': 'airport',
  'source': 'OurAirports',
  'geohash': 'szsrjjzd02b3'},
 'dst_airport': {'airport_id': 2990,
  'name': 'Kazan International Airport',
  'city': 'Kazan',
  'country': 'Russia',
  'iata': 'KZN',
  'icao': 'UWKD',
  'latitude': 55.606201171875,
  'longitude': 49.278701782227,
  'altitude': 411,
  'timezone': 3.0,
  'dst': 'N',
  'tz_id': 'Europe/Moscow',
  'type': 'airport',
  'source': 'OurAirports'},
 'codeshare': False,
 'equipment': ['CR2']}

In [27]:
airport = geo_records[0]['src_airport']
airport
# if airport:
#     print(airport)

{'airport_id': 2965,
 'name': 'Sochi International Airport',
 'city': 'Sochi',
 'country': 'Russia',
 'iata': 'AER',
 'icao': 'URSS',
 'latitude': 43.449902,
 'longitude': 39.9566,
 'altitude': 89,
 'timezone': 3.0,
 'dst': 'N',
 'tz_id': 'Europe/Moscow',
 'type': 'airport',
 'source': 'OurAirports',
 'geohash': 'szsrjjzd02b3'}

In [24]:
airport['latitude']

43.449902

In [37]:
airportHash = pygeohash.encode(airport['latitude'], airport['longitude'])
airportHash

'szsrjjzd02b3'

In [43]:
homeHash = pygeohash.encode(lat, lon)
distToLoc = pygeohash.geohash_approximate_distance(homeHash, airportHash)/1000
distToLoc

20000.0

In [44]:
airportList = []
if distToLoc < dist:
    airportList.append(airport['name'])

In [45]:
airportList

[]

In [ ]:
hashes = sorted(list(hash_set))

In [ ]:
airportSet.add()

In [46]:
record = geo_records[0]

In [48]:
record['src_airport']

{'airport_id': 2965,
 'name': 'Sochi International Airport',
 'city': 'Sochi',
 'country': 'Russia',
 'iata': 'AER',
 'icao': 'URSS',
 'latitude': 43.449902,
 'longitude': 39.9566,
 'altitude': 89,
 'timezone': 3.0,
 'dst': 'N',
 'tz_id': 'Europe/Moscow',
 'type': 'airport',
 'source': 'OurAirports',
 'geohash': 'szsrjjzd02b3'}

In [59]:
def airport_search(latitude=41.1499988, longitude=-95.91779, distance=1000):
    ## TODO: Create simple search to return nearest airport
    homeHash = pygeohash.encode(latitude, longitude)
    airportSet = set()
    for record in geo_records:
        airport = record['src_airport']
        if airport:
            airportHash = pygeohash.encode(airport['latitude'], airport['longitude'])
            distToLoc = pygeohash.geohash_approximate_distance(homeHash, airportHash)/1000
            if distToLoc <= distance:
                airportSet.add(airport['name'])
    airportList = sorted(list(airportSet))
    
    print(f'The following airports are within {distance} km of ({latitude}, {longitude}):\n')
    for airport in airportList:
        print(' -', airport)
#     pass

In [61]:
# airport_search()

In [62]:
lat = float(input("Enter your latitude:\t"))
lon = float(input("Enter your longitude:\t"))
dist = float(input("Input search radius (km): "))

airport_search(lat, lon, dist)

Enter your latitude:	40.787560
Enter your longitude:	-96.743690
Input search radius (km): 200
The following airports are within 200.0 km of (40.78756, -96.74369):

 - Eppley Airfield
 - Lincoln Airport


In [63]:
homeHash

'9z7f174u17zb'

In [66]:
for record in geo_records:
    airport = record['src_airport']
    if airport:
        if airport['name'] == 'Des Moines International Airport':
            dsmHash = pygeohash.encode(airport['latitude'], airport['longitude'])
dsmHash

'9zmkk9h95dcg'

In [69]:
distToLoc = pygeohash.geohash_approximate_distance(homeHash, dsmHash)/1000
distToLoc

625.441